In [1]:
import json
import os
from pprint import pprint

import bitsandbytes as bnb
import pandas as pd
import torch
import torch.nn as nn

import transformers
from datasets import load_dataset
from huggingface_hub import notebook_login
from peft import (
    LoraConfig,
    PeftConfig,
    PeftModel,
    get_peft_model,
    prepare_model_for_kbit_training,
)
from transformers import (
    AutoConfig,
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
)
import warnings
warnings.filterwarnings("ignore")

os.environ["CUDA_VISIBLE_DEVICES"] = "0"


===================================BUG REPORT===================================
Welcome to bitsandbytes. For bug reports, please run

python -m bitsandbytes

 and submit this information together with your error trace to: https://github.com/TimDettmers/bitsandbytes/issues
bin /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda121.so
CUDA_SETUP: WARNING! libcudart.so not found in any environmental path. Searching in backup paths...
CUDA SETUP: CUDA runtime path found: /usr/local/cuda/lib64/libcudart.so
CUDA SETUP: Highest compute capability among GPUs detected: 8.6
CUDA SETUP: Detected CUDA version 121
CUDA SETUP: Loading binary /opt/conda/lib/python3.10/site-packages/bitsandbytes/libbitsandbytes_cuda121.so...


/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('/usr/local/nvidia/lib'), PosixPath('/usr/local/nvidia/lib64')}
  warn(msg)
/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: /usr/local/nvidia/lib:/usr/local/nvidia/lib64 did not contain ['libcudart.so', 'libcudart.so.11.0', 'libcudart.so.12.0'] as expected! Searching further paths...
  warn(msg)
/opt/conda/lib/python3.10/site-packages/bitsandbytes/cuda_setup/main.py:149: UserWarning: WARNING: The following directories listed in your path were found to be non-existent: {PosixPath('ssh-rsa AAAAB3NzaC1yc2EAAAADAQABAAACAQCcuY6EsmJRfLsI1l1rpDWVRhwkL7A9nzITTDbCFOX0wzshP65l/Sa54NrS1pX2uM6YiB7OvgGUm7uUKf9OBCcpd2ohFJiOkTznhDHk+D7IkFZf/VTRIHy/JZoAtzN/qBQKMOygFam1XzTMDnkehMkKvR23BgH72hzGUfYPIsq+OlStYVMhE1bncYSnC4SRucbdT5BeIsival514xsbAhCjjwPd8UHfw1cxaDq4edWjbhN8wkDU+V8i/j

In [2]:
notebook_login()

In [3]:
with open("ds1000-test-cleaned.json") as json_file:
    data = json.load(json_file)

In [4]:
pprint(data[0])

{'answer': 'import pandas as pd\n'
           '\n'
           '\n'
           'index = range(14)\n'
           'data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]\n'
           "df = pd.DataFrame(data=data, index=index, columns = ['A'])\n"
           'def g(df):\n'
           "    l = df['A'].replace(to_replace=0, method='ffill')\n"
           "    r = df['A'].replace(to_replace=0, method='bfill')\n"
           '    for i in range(len(df)):\n'
           "        df['A'].iloc[i] = max(l[i], r[i])\n"
           '    return df\n'
           '\n'
           'df = g(df.copy())\n'
           'result = df\n'
           'print(result)',
 'question': 'Problem:\n'
             'I have the following dataframe:\n'
             'index = range(14)\n'
             'data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]\n'
             "df = pd.DataFrame(data=data, index=index, columns = ['A'])\n"
             '\n'
             '\n'
             'How can I fill the zeros with the maximun between previous a

In [5]:
with open("ds1000-test-cleaned.json", "w") as f:
    json.dump(data, f)

In [6]:
pd.DataFrame(data).head()

question  \
0  Problem:\nI have the following dataframe:\nind...   
1  Problem:\ni got an issue over ranking of date ...   
2  Problem:\nI have a DataFrame like :\n     0   ...   
3  Problem:\nI have this Pandas dataframe (df):\n...   
4  Problem:\nI have\n\ndf = pd.DataFrame.from_dic...   

                                              answer  
0  import pandas as pd\n\n\nindex = range(14)\nda...  
1  import pandas as pd\n\n\ndf = pd.DataFrame({'I...  
2  import pandas as pd\nimport numpy as np\n\ndf ...  
3  import pandas as pd\n\n\ndf = pd.DataFrame({'A...  
4  import pandas as pd\n\ndf = pd.DataFrame.from_...

In [7]:
bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_use_double_quant=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16,
)

In [8]:
PEFT_MODEL = "shanjay/ds-dsc-v4"

config = PeftConfig.from_pretrained(PEFT_MODEL)
model = AutoModelForCausalLM.from_pretrained(
    config.base_model_name_or_path,
    return_dict=True,
    quantization_config=bnb_config,
    device_map="auto",
    trust_remote_code=True,
)
tokenizer = AutoTokenizer.from_pretrained(config.base_model_name_or_path)
tokenizer.pad_token = tokenizer.eos_token

model = PeftModel.from_pretrained(model, PEFT_MODEL)

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

Some weights of LlamaForCausalLM were not initialized from the model checkpoint at deepseek-ai/deepseek-coder-6.7b-instruct and are newly initialized: ['model.layers.17.self_attn.rotary_emb.inv_freq', 'model.layers.4.self_attn.rotary_emb.inv_freq', 'model.layers.12.self_attn.rotary_emb.inv_freq', 'model.layers.29.self_attn.rotary_emb.inv_freq', 'model.layers.20.self_attn.rotary_emb.inv_freq', 'model.layers.15.self_attn.rotary_emb.inv_freq', 'model.layers.21.self_attn.rotary_emb.inv_freq', 'model.layers.19.self_attn.rotary_emb.inv_freq', 'model.layers.23.self_attn.rotary_emb.inv_freq', 'model.layers.30.self_attn.rotary_emb.inv_freq', 'model.layers.3.self_attn.rotary_emb.inv_freq', 'model.layers.18.self_attn.rotary_emb.inv_freq', 'model.layers.6.self_attn.rotary_emb.inv_freq', 'model.layers.1.self_attn.rotary_emb.inv_freq', 'model.layers.31.self_attn.rotary_emb.inv_freq', 'model.layers.28.self_attn.rotary_emb.inv_freq', 'model.layers.14.self_attn.rotary_emb.inv_freq', 'model.layers.0.sel

adapter_model.bin:   0%|          | 0.00/33.6M [00:00<?, ?B/s]

In [9]:
generation_config = model.generation_config
generation_config.max_new_tokens = 200
generation_config.temperature = 0.7
generation_config.top_p = 0.7
generation_config.num_return_sequences = 1
generation_config.pad_token_id = tokenizer.eos_token_id
generation_config.eos_token_id = tokenizer.eos_token_id

In [10]:
DEVICE = "cuda:0"

In [11]:
%%time
prompt = f"""
<instruction>: How can I create a dataframe?
<output>:
""".strip()

encoding = tokenizer(prompt, return_tensors="pt").to(DEVICE)
with torch.inference_mode():
    outputs = model.generate(
        input_ids=encoding.input_ids,
        attention_mask=encoding.attention_mask,
        generation_config=generation_config,
    )
print(tokenizer.decode(outputs[0], skip_special_tokens=True))

<instruction>: How can I create a dataframe?
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A  B
0  1  4
1  2  5
2  3  6
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A  B
0  1  4
1  2  5
2  3  6
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A
CPU times: user 26.8 s, sys: 346 ms, total: 27.1 s
Wall time: 27.2 s


In [12]:
def generate_response(question: str) -> str:
    prompt = f"""
<instruction>: {question}
<output>:
""".strip()
    encoding = tokenizer(prompt, return_tensors="pt").to(DEVICE)
    with torch.inference_mode():
        outputs = model.generate(
            input_ids=encoding.input_ids,
            attention_mask=encoding.attention_mask,
            generation_config=generation_config,
        )
    response = tokenizer.decode(outputs[0], skip_special_tokens=True)

    assistant_start = "<output>:"
    response_start = response.find(assistant_start)
    return response[response_start + len(assistant_start) :].strip()

In [13]:
prompt = "How can I create a dataframe?"
print(generate_response(prompt))

import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A  B
0  1  4
1  2  5
2  3  6
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A  B
0  1  4
1  2  5
2  3  6
<output>: import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
print(df)
   A


In [14]:
prompt = "How to merge two dataframes?"
print(generate_response(prompt))

import pandas as pd

df1 = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]})
df2 = pd.DataFrame({'C': [7, 8, 9], 'D': [10, 11, 12]})

# merge df1 and df2
result = ...

print(result)

# Expected output
#   A  B  C  D
# 0  1  4  7 10
# 1  2  5  8 11
# 2  3  6  9 12
<output>: import pandas as pd

df1 = pd.DataFrame({'A': [1, 2, 3], 'B': [4, 5, 6]


In [15]:
prompt = "given two arrays name=['joy','shan'], roll_no=[1,2]. put these array in a dataframe ?"
print(generate_response(prompt))

import pandas as pd


name=['joy','shan']
roll_no=[1,2]
df = pd.DataFrame({'name': name, 'roll_no': roll_no})
print(df)


   name  roll_no
0  joy         1
1  shan        2
<output>: import pandas as pd


name=['joy','shan']
roll_no=[1,2]
df = pd.DataFrame({'name': name, 'roll_no': roll_no})
print(df)


   name  roll_no
0  joy         1
1  shan        2
<output>: import pandas as pd


name=['joy','shan']
roll_no=[1,2]
df = pd.DataFrame({


In [16]:
prompt = "can you plot all types of plots in matplotlib?"
print(generate_response(prompt))

import matplotlib.pyplot as plt

x = range(10)
y = range(10)

plt.plot(x, y, label='line')
plt.scatter(x, y, label='scatter')
plt.bar(x, y, label='bar')
plt.hist(x, y, label='hist')
plt.legend()
plt.show()
<output>: import matplotlib.pyplot as plt

x = range(10)
y = range(10)

plt.plot(x, y, label='line')
plt.scatter(x, y, label='scatter')
plt.bar(x, y, label='bar')
plt.hist(x, y, label='hist')
pl


In [19]:
prompt = """Problem:
i got an issue over ranking of date times. Lets say i have following table.
ID    TIME
01    2018-07-11 11:12:20
01    2018-07-12 12:00:23
01    2018-07-13 12:00:00
02    2019-09-11 11:00:00
02    2019-09-12 12:00:00


and i want to add another column to rank the table by time for each id and group. I used 
df['RANK'] = data.groupby('ID')['TIME'].rank(ascending=True)


but get an error:
'NoneType' object is not callable


If i replace datetime to numbers, it works.... any solutions?
"""
print(generate_response(prompt))

!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!


In [20]:
prompt = """Problem:
I have the following dataframe:
index = range(14)
data = [1, 0, 0, 2, 0, 4, 6, 8, 0, 0, 0, 0, 2, 1]
df = pd.DataFrame(data=data, index=index, columns = ['A'])


How can I fill the zeros with the maximun between previous and posterior non-zero value using pandas? Is there a fillna that is not just for "NaN"?.  
The output should look like:
    A
0   1
1   2
2   2
3   2
4   4
5   4
6   6
7   8
8   8
9   8
10  8
11  8
12  2
13  1
"""

print(generate_response(prompt))

!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!


In [27]:
print(data[5]['question'])

Problem:
My sample df has four columns with NaN values. The goal is to concatenate all the keywords rows while excluding the NaN values.
import pandas as pd
import numpy as np
df = pd.DataFrame({'users': ['Hu Tao', 'Zhongli', 'Xingqiu'],
                   'keywords_0': ["a", np.nan, "c"],
                   'keywords_1': ["d", "e", np.nan],
                   'keywords_2': [np.nan, np.nan, "b"],
                   'keywords_3': ["f", np.nan, "g"]})


     users keywords_0 keywords_1 keywords_2 keywords_3
0   Hu Tao          a          d        NaN          f
1  Zhongli        NaN          e        NaN        NaN
2  Xingqiu          c        NaN          b          g


Want to accomplish the following:
     users keywords_0 keywords_1 keywords_2 keywords_3 keywords_all
0   Hu Tao          a          d        NaN          f        a-d-f
1  Zhongli        NaN          e        NaN        NaN            e
2  Xingqiu          c        NaN          b          g        c-b-g


Pseudo code:
c

In [28]:
print(data[5]['answer'])

import pandas as pd
import numpy as np


df = pd.DataFrame({'users': ['Hu Tao', 'Zhongli', 'Xingqiu'],
                   'keywords_0': ["a", np.nan, "c"],
                   'keywords_1': ["d", "e", np.nan],
                   'keywords_2': [np.nan, np.nan, "b"],
                   'keywords_3': ["f", np.nan, "g"]})
import numpy as np
def g(df):
    df["keywords_all"] = df.filter(like='keyword').apply(lambda x: '-'.join(x.dropna()), axis=1)
    return df

df = g(df.copy())
result = df
print(result)


In [29]:
prompt = data[5]['question']
print(generate_response(prompt))

!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!


In [30]:
prompt = "How to remove null valued rows?"
print(generate_response(prompt))

import pandas as pd


df = pd.DataFrame({'A': [1, 2, 3, None, 5],
                   'B': [1, 2, 3, None, 5],
                   'C': [1, 2, 3, None, 5],
                   'D': [1, 2, 3, None, 5],
                   'E': [1, 2, 3, None, 5]})

df = df.dropna(how='all')
print(df)
<output>:   A  B  C  D  E
0  1  1  1  1  1
1  2  2  2  2  2
2  3  3  3  3  3
4  5  5  5  5  5
<output>: import pand
